In [70]:
#catboost and random forest only with feature engineering
import os
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt

In [71]:
os.chdir('D:\\Hackathon')

In [72]:
os.getcwd()

'D:\\Hackathon'

In [73]:
train = pd.read_csv('train.csv')
test = pd.read_csv('test.csv')

In [74]:
train['number_of_borrowers'] = train['number_of_borrowers'].astype('int64')

In [75]:
train['origination_date'].head()

0    2012-03-01
1    2012-01-01
2    2012-01-01
3    2012-02-01
4    2012-02-01
Name: origination_date, dtype: object

In [76]:
train['m13'].value_counts()
train['number_of_borrowers'] = train['number_of_borrowers'].astype('category')
test['number_of_borrowers'] = test['number_of_borrowers'].astype('category')

In [77]:
#undersampling of data
from sklearn.utils import resample
df_majority = train[train.m13==0]
df_minority1 = train[train.m13==1] 
# Downsample majority class
df_majority_downsampled = resample(df_majority,
                                 replace=False,    # sample without replacement
                                 n_samples=20000,     # to match minority class
                                 random_state=42) # reproducible results
 
# Combine minority class with downsampled majority class
train = pd.concat([df_majority_downsampled, df_minority1])
 
# Display new class counts
print(train.m13.value_counts())
train.reset_index(inplace = True)
train.drop(['index'],axis = 1,inplace = True)

0    20000
1      636
Name: m13, dtype: int64


In [459]:
#profile report for eda
import pandas_profiling as pp
pp.ProfileReport(train)

In [78]:
#feature engineering.
train['origination_date'] = pd.to_datetime(train['origination_date'])
train['first_payment_date'] = pd.to_datetime(train['first_payment_date'])

In [79]:
train['first_payment_month'] = train['first_payment_date'].dt.month.astype('category')
train['origination_month'] = train['origination_date'].dt.month.astype('category')

In [80]:
train.drop(['origination_date','first_payment_date'],axis =1 , inplace = True)

In [81]:
from datetime import datetime
test['first_payment_date'] = [datetime.strptime(i, '%b-%y') for i in test['first_payment_date']]

In [82]:
test['origination_date'] = pd.to_datetime(test['origination_date'],format = '%d/%m/%y')
#test['first_payment_date'] = pd.to_datetime(test['first_payment_date'])
test['first_payment_month'] = test['first_payment_date'].dt.month.astype('category')
test['origination_month'] = test['origination_date'].dt.month.astype('category')
test.drop(['origination_date','first_payment_date'],axis =1 , inplace = True)

In [83]:
train.tail()

loan_id source       financial_institution  interest_rate  \
20631  164429891592      X                       OTHER          3.375   
20632  443805676916      X                       OTHER          2.875   
20633  455486579921      X    Martinez, Duffy and Bird          3.500   
20634  459681531406      X  Swanson, Newton and Miller          4.500   
20635  583413529768      Y             Edwards-Hoffman          4.375   

       unpaid_principal_bal  loan_term  loan_to_value number_of_borrowers  \
20631                 75000        180             27                   1   
20632                332000        180             79                   2   
20633                 70000        180             11                   1   
20634                 82000        360             23                   1   
20635                232000        240             75                   1   

       debt_to_income_ratio  borrower_credit_score loan_purpose  \
20631                  32.0                  683.0          B12   
20632                  44.0                  662.0          A23   
20633                  40.0                  663.0          B12   
20634                  42.0                  767.0          A23   
20635                  39.0                  674.0          A23   

       insurance_percent  co-borrower_credit_score  insurance_type  m1  m2  \
20631                0.0                       0.0             0.0   0   0   
20632                0.0                     658.0             0.0   0   0   
20633                0.0                       0.0             0.0   0   0   
20634                0.0                       0.0             0.0   0   0   
20635                0.0                       0.0             0.0   0   0   

       m3  m4  m5  m6  m7  m8  m9  m10  m11  m12  m13 first_payment_month  \
20631   0   0   0   0   0   1   1    0    0    0    1                   3   
20632   0   0   0   0   0   0   0    0    0    0    1                   5   
20633   0   0   0   1   0   0   1    1    1    2    1                   4   
20634   0   0   0   0   0   0   0    0    0    0    1                   4   
20635   0   0   0   0   0   0   0    0    0    0    1                   3   

      origination_month  
20631                 1  
20632                 3  
20633                 2  
20634                 2  
20635                 1

In [84]:
train['both_credit_score'] = train['borrower_credit_score'] + train['co-borrower_credit_score']
test['both_credit_score'] = test['borrower_credit_score'] + test['co-borrower_credit_score']

In [85]:
#train['interest_rate_fraction'] = train['interest_rate'] % 1
#test['interest_rate_fraction'] = test['interest_rate'] %1

In [86]:
train['q1'] = train['m1'] + train['m2'] + train['m3']
train['q2'] =  train['m4'] + train['m5'] +train['m6']
train['q3'] = train['m7'] + train['m8'] + train['m9'] 
train['q4'] =  train['m10'] + train['m11'] +train['m12']

In [87]:
test['q1'] = test['m1'] + test['m2'] + test['m3']
test['q2'] =  test['m4'] + test['m5'] +test['m6']
test['q3'] = test['m7'] + test['m8'] + test['m9'] 
test['q4'] =  test['m10'] + test['m11'] +test['m12']

In [88]:
train['s1'] = train['q1'] +train['q2']
train['s2'] = train['q3']+train['q4']
test['s1'] = test['q1'] +test['q2'] 
test['s2'] = test['q3']+test['q4'] 

In [89]:
train['concat1']= train['source'].str.cat(train['number_of_borrowers'].map(str))
test['concat1'] = test['source'].str.cat(test['number_of_borrowers'].map(str))

In [90]:
train['concat3']= train['loan_purpose'].str.cat(train['number_of_borrowers'].map(str))
test['concat3'] = test['loan_purpose'].str.cat(test['number_of_borrowers'].map(str))

In [91]:
category = ['source','financial_institution','loan_purpose','concat1','concat3']
for i in category:
    test[i] = test[i].astype('category')
    train[i] = train[i].astype('category')

In [92]:
train.drop(['insurance_type'],axis =1 , inplace = True)
test.drop(['insurance_type'],axis = 1, inplace = True)

In [93]:
#for feature selection of categorical and numerical problems
import statsmodels.formula.api as smf
anova1 = smf.ols(formula='unpaid_principal_bal~ m13',data = train).fit()
print (anova1.f_pvalue)
anova2 = smf.ols(formula='loan_term~ m13',data = train).fit()
print (anova2.f_pvalue)
anova3 = smf.ols(formula='loan_to_value~ m13',data = train).fit()
print (anova3.f_pvalue)
anova4 = smf.ols(formula='debt_to_income_ratio~ m13',data = train).fit()
print (anova4.f_pvalue)
anova5 = smf.ols(formula='insurance_percent~ m13',data = train).fit()
print (anova5.f_pvalue)




9.656804290119517e-09
6.417060889803163e-16
1.6930259599218753e-07
3.080771889890868e-38
0.10201600752428765


In [94]:
from scipy.stats import chi2_contingency
cat_names = ["source", "financial_institution","number_of_borrowers", "loan_purpose", "first_payment_month", "origination_month",'concat1','concat3']
for i in cat_names:
    print (i)
    chi2,p,dof,ex = chi2_contingency(pd.crosstab(train[i],train['m13']))
    print (i +" " + str(p))

source
source 0.0008841627252478061
financial_institution
financial_institution 0.08256723339932781
number_of_borrowers
number_of_borrowers 4.4185549082440493e-41
loan_purpose
loan_purpose 1.9625127399229123e-16
first_payment_month
first_payment_month 0.00025513257516407103
origination_month
origination_month 0.000493471481888547
concat1
concat1 3.2885363313010696e-41
concat3
concat3 2.556126186733936e-59


In [95]:
train.drop(['financial_institution','insurance_percent'],axis = 1,inplace = True)
test.drop(['financial_institution','insurance_percent'],axis = 1,inplace = True)

In [96]:
pd.set_option('display.max_columns',80)
train.drop(['m11'],axis = 1, inplace = True)
test.drop(['m11'],axis = 1, inplace = True)

In [97]:
averages = train.groupby(by = train['source'])['m13'].agg(["mean", "count"])

In [98]:
#was trying to do mean encoding but ut generally overfitting the data
#train['source'] = train['source'].replace(['X','Y','Z'],[0.026908,0.036794,0.032457])
#test['source'] = test['source'].replace(['X','Y','Z'],[0.026908,0.036794,0.032457])

In [99]:
averages1 = train.groupby(by = train['loan_purpose'])['unpaid_principal_bal'].agg(["mean"])

In [100]:
#train['concat3']= train['source'].str.cat(train['loan_purpose'].map(str))
#test['concat3'] = test['source'].str.cat(test['loan_purpose'].map(str))

In [101]:
train['gap_between_first1'] = train['first_payment_month'].astype('int64') + train['origination_month'].astype('int64')
test['gap_between_first1'] = test['first_payment_month'].astype('int64') + test['origination_month'].astype('int64')

In [102]:
#train['gap_between_first'] = train['first_payment_month'].astype('int64') - train['origination_month'].astype('int64')
#test['gap_between_first'] = test['first_payment_month'].astype('int64') - test['origination_month'].astype('int64')

In [103]:
#train['number_of_borrowers'] = train['number_of_borrowers'].replace([1,2],[0.050147,0.017243])
#test['number_of_borrowers'] = test['number_of_borrowers'].replace([1,2],[0.050147,0.017243])
train.head()

loan_id source  interest_rate  unpaid_principal_bal  loan_term  \
0  620750452604      X          3.500                233000        240   
1  741971052978      X          3.375                155000        180   
2  182288891988      X          3.625                160000        360   
3  479418941832      X          3.250                201000        180   
4  588213683587      Y          4.000                417000        360   

   loan_to_value number_of_borrowers  debt_to_income_ratio  \
0             72                   1                  21.0   
1             68                   2                  44.0   
2             75                   1                  35.0   
3             30                   1                  10.0   
4             75                   1                  39.0   

   borrower_credit_score loan_purpose  co-borrower_credit_score  m1  m2  m3  \
0                  805.0          A23                       0.0   0   0   0   
1                  719.0          A23                     768.0   0   0   0   
2                  685.0          A23                       0.0   0   0   0   
3                  743.0          B12                       0.0   0   0   0   
4                  760.0          B12                       0.0   0   0   0   

   m4  m5  m6  m7  m8  m9  m10  m12  m13 first_payment_month  \
0   0   0   0   0   0   0    0    0    0                   3   
1   0   0   0   0   0   0    0    0    0                   4   
2   0   0   0   0   0   0    0    0    0                   4   
3   0   0   0   0   0   0    0    0    0                   4   
4   0   0   0   0   0   0    0    0    0                   3   

  origination_month  both_credit_score  q1  q2  q3  q4  s1  s2 concat1  \
0                 1              805.0   0   0   0   0   0   0      X1   
1                 2             1487.0   0   0   0   0   0   0      X2   
2                 2              685.0   0   0   0   0   0   0      X1   
3                 2              743.0   0   0   0   0   0   0      X1   
4                 1              760.0   0   0   0   0   0   0      Y1   

  concat3  gap_between_first1  
0    A231                   4  
1    A232                   6  
2    A231                   6  
3    B121                   6  
4    B121                   4

In [104]:
averages = train.groupby(by = train['loan_purpose'])['m13'].agg(["mean", "count"])

In [105]:
averages

mean  count
loan_purpose                 
A23           0.020555  10265
B12           0.041882   5229
C86           0.040062   5142

In [106]:
#train['loan_purpose'] = train['loan_purpose'].replace(['A23','B12','C86'],[0.020555,0.041882,0.040062])
#test['loan_purpose'] = test['loan_purpose'].replace(['A23','B12','C86'],[0.020555,0.041882,0.040062])

In [107]:
train['loan_purpose'].value_counts()

A23    10265
B12     5229
C86     5142
Name: loan_purpose, dtype: int64

In [108]:
train = pd.get_dummies(train)
test = pd.get_dummies(test)

In [109]:
from sklearn.model_selection import train_test_split

In [110]:
test1 = test.copy()
train.drop(['loan_id'],axis = 1,inplace = True)
test.drop(['loan_id'],axis =1, inplace = True)

In [111]:
train.shape

(20636, 54)

In [112]:
test.shape

(35866, 53)

In [113]:
train, test_x = train_test_split(train, test_size = 0.20, random_state = 42,stratify = train['m13'])

In [114]:
y_label = train['m13']
test_label = test_x['m13']

In [115]:
train.drop(['m13'],axis =1,inplace = True)
test_x.drop(['m13'],axis =1,inplace = True)

In [116]:
from sklearn.metrics import classification_report

In [117]:
from sklearn.naive_bayes import ComplementNB

In [118]:
cnb = ComplementNB(fit_prior = True).fit(train,y_label)
predict_cnb = cnb.predict(test_x)

pd.crosstab(test_label,predict_cnb)

col_0     0     1
m13              
0      2351  1650
1        42    85

In [119]:
print (classification_report(test_label,predict_cnb))

              precision    recall  f1-score   support

           0       0.98      0.59      0.74      4001
           1       0.05      0.67      0.09       127

   micro avg       0.59      0.59      0.59      4128
   macro avg       0.52      0.63      0.41      4128
weighted avg       0.95      0.59      0.72      4128



In [120]:
from sklearn.tree import DecisionTreeClassifier
dt = DecisionTreeClassifier(max_depth = 7).fit(train,y_label)
predict_dt = dt.predict(test_x)
pd.crosstab(test_label,predict_dt)
predict_dt_t = dt.predict(train)

In [121]:
print (classification_report(test_label,predict_dt))

              precision    recall  f1-score   support

           0       0.99      1.00      0.99      4001
           1       0.82      0.54      0.65       127

   micro avg       0.98      0.98      0.98      4128
   macro avg       0.90      0.77      0.82      4128
weighted avg       0.98      0.98      0.98      4128



In [122]:
from sklearn.ensemble import RandomForestClassifier
rfc = RandomForestClassifier(max_depth = 8,n_estimators = 250,n_jobs = -1).fit(train,y_label)
predict_rfc = rfc.predict(test_x)
pd.crosstab(test_label,predict_rfc)
predict_rfc_t = rfc.predict(train)

In [123]:
print (classification_report(test_label,predict_rfc))

              precision    recall  f1-score   support

           0       0.99      1.00      0.99      4001
           1       0.86      0.56      0.68       127

   micro avg       0.98      0.98      0.98      4128
   macro avg       0.92      0.78      0.83      4128
weighted avg       0.98      0.98      0.98      4128



In [792]:
#from sklearn.svm import SVC
#model_sv = SVC(kernel = 'linear',C= 2, gamma = 0.1).fit(train,y_label)
#predict_svm = model_sv.predict(test_x)
#pd.crosstab(test_label,predict_svm)

In [793]:
#print (classification_report(test_label,predict_svm))

In [65]:
import xgboost as xgb
model_xg = xgb.XGBClassifier( learning_rate = 0.9,
           max_depth = 8,
          gamma = 1.1,
          alpha = 10,
          n_estimators = 200,objective = 'multi:softmax',num_class = 2,eval_metric ='merror',colsample_bytree = 0.7,n_jobs =-1)
model_xg.fit(train,y_label)
predict_xg = model_xg.predict(test_x)
pd.crosstab(test_label,predict_xg)
#predict_xg_t = model_xg.predict(train)

col_0     0   1
m13            
0      3987  14
1        57  70

In [66]:
print (classification_report(test_label,predict_xg))

              precision    recall  f1-score   support

           0       0.99      1.00      0.99      4001
           1       0.83      0.55      0.66       127

   micro avg       0.98      0.98      0.98      4128
   macro avg       0.91      0.77      0.83      4128
weighted avg       0.98      0.98      0.98      4128



In [67]:
# cat boost model
from catboost import CatBoostClassifier
model_cb = CatBoostClassifier(learning_rate = 0.01,iterations = 800,depth =7, eval_metric = 'F1').fit(train,y_label)
predict_cb = model_cb.predict(test_x)
predict_cb = predict_cb.flatten()
pd.crosstab(test_label,predict_cb)
#predict_cb_t = model_cb.predict(train)
#predict_cb_t = predict_cb_t.flatten()

0:	learn: 0.6161027	total: 234ms	remaining: 3m 6s
1:	learn: 0.6400000	total: 337ms	remaining: 2m 14s
2:	learn: 0.6345178	total: 421ms	remaining: 1m 51s
3:	learn: 0.6329114	total: 520ms	remaining: 1m 43s
4:	learn: 0.6203346	total: 612ms	remaining: 1m 37s
5:	learn: 0.5710383	total: 698ms	remaining: 1m 32s
6:	learn: 0.6055777	total: 810ms	remaining: 1m 31s
7:	learn: 0.6159895	total: 906ms	remaining: 1m 29s
8:	learn: 0.6219355	total: 1.01s	remaining: 1m 29s
9:	learn: 0.6229086	total: 1.12s	remaining: 1m 28s
10:	learn: 0.6157895	total: 1.19s	remaining: 1m 25s
11:	learn: 0.5784447	total: 1.28s	remaining: 1m 24s
12:	learn: 0.5872801	total: 1.4s	remaining: 1m 24s
13:	learn: 0.5921938	total: 1.48s	remaining: 1m 23s
14:	learn: 0.6178010	total: 1.58s	remaining: 1m 22s
15:	learn: 0.5815217	total: 1.64s	remaining: 1m 20s
16:	learn: 0.5803815	total: 1.74s	remaining: 1m 20s
17:	learn: 0.5834464	total: 1.85s	remaining: 1m 20s
18:	learn: 0.5834464	total: 1.96s	remaining: 1m 20s
19:	learn: 0.5818674	tot

158:	learn: 0.6625464	total: 15.9s	remaining: 1m 4s
159:	learn: 0.6625464	total: 16.1s	remaining: 1m 4s
160:	learn: 0.6625464	total: 16.1s	remaining: 1m 4s
161:	learn: 0.6625464	total: 16.2s	remaining: 1m 3s
162:	learn: 0.6625464	total: 16.3s	remaining: 1m 3s
163:	learn: 0.6625464	total: 16.4s	remaining: 1m 3s
164:	learn: 0.6625464	total: 16.5s	remaining: 1m 3s
165:	learn: 0.6625464	total: 16.6s	remaining: 1m 3s
166:	learn: 0.6625464	total: 16.7s	remaining: 1m 3s
167:	learn: 0.6625464	total: 16.8s	remaining: 1m 3s
168:	learn: 0.6625464	total: 16.9s	remaining: 1m 3s
169:	learn: 0.6625464	total: 17s	remaining: 1m 2s
170:	learn: 0.6625464	total: 17.1s	remaining: 1m 2s
171:	learn: 0.6625464	total: 17.2s	remaining: 1m 2s
172:	learn: 0.6625464	total: 17.3s	remaining: 1m 2s
173:	learn: 0.6625464	total: 17.4s	remaining: 1m 2s
174:	learn: 0.6625464	total: 17.5s	remaining: 1m 2s
175:	learn: 0.6625464	total: 17.6s	remaining: 1m 2s
176:	learn: 0.6625464	total: 17.7s	remaining: 1m 2s
177:	learn: 0.

318:	learn: 0.6715867	total: 31.1s	remaining: 46.9s
319:	learn: 0.6715867	total: 31.2s	remaining: 46.8s
320:	learn: 0.6715867	total: 31.3s	remaining: 46.7s
321:	learn: 0.6715867	total: 31.4s	remaining: 46.6s
322:	learn: 0.6715867	total: 31.5s	remaining: 46.5s
323:	learn: 0.6732429	total: 31.6s	remaining: 46.4s
324:	learn: 0.6732429	total: 31.7s	remaining: 46.3s
325:	learn: 0.6732429	total: 31.8s	remaining: 46.2s
326:	learn: 0.6732429	total: 31.9s	remaining: 46.1s
327:	learn: 0.6732429	total: 32s	remaining: 46s
328:	learn: 0.6732429	total: 32s	remaining: 45.8s
329:	learn: 0.6732429	total: 32.1s	remaining: 45.7s
330:	learn: 0.6732429	total: 32.2s	remaining: 45.6s
331:	learn: 0.6732429	total: 32.3s	remaining: 45.5s
332:	learn: 0.6732429	total: 32.4s	remaining: 45.4s
333:	learn: 0.6740741	total: 32.5s	remaining: 45.3s
334:	learn: 0.6740741	total: 32.6s	remaining: 45.2s
335:	learn: 0.6732429	total: 32.6s	remaining: 45.1s
336:	learn: 0.6740741	total: 32.7s	remaining: 45s
337:	learn: 0.673242

478:	learn: 0.6854345	total: 46s	remaining: 30.8s
479:	learn: 0.6870416	total: 46.1s	remaining: 30.7s
480:	learn: 0.6870416	total: 46.2s	remaining: 30.6s
481:	learn: 0.6870416	total: 46.3s	remaining: 30.5s
482:	learn: 0.6870416	total: 46.4s	remaining: 30.4s
483:	learn: 0.6870416	total: 46.5s	remaining: 30.3s
484:	learn: 0.6870416	total: 46.6s	remaining: 30.3s
485:	learn: 0.6870416	total: 46.7s	remaining: 30.2s
486:	learn: 0.6870416	total: 46.8s	remaining: 30.1s
487:	learn: 0.6870416	total: 46.9s	remaining: 30s
488:	learn: 0.6870416	total: 46.9s	remaining: 29.9s
489:	learn: 0.6870416	total: 47s	remaining: 29.8s
490:	learn: 0.6870416	total: 47.1s	remaining: 29.7s
491:	learn: 0.6870416	total: 47.2s	remaining: 29.6s
492:	learn: 0.6870416	total: 47.3s	remaining: 29.5s
493:	learn: 0.6870416	total: 47.4s	remaining: 29.4s
494:	learn: 0.6870416	total: 47.5s	remaining: 29.3s
495:	learn: 0.6870416	total: 47.6s	remaining: 29.2s
496:	learn: 0.6870416	total: 47.7s	remaining: 29.1s
497:	learn: 0.6870

638:	learn: 0.6974484	total: 1m	remaining: 15.3s
639:	learn: 0.6974484	total: 1m	remaining: 15.2s
640:	learn: 0.6974484	total: 1m 1s	remaining: 15.1s
641:	learn: 0.6974484	total: 1m 1s	remaining: 15s
642:	learn: 0.6974484	total: 1m 1s	remaining: 14.9s
643:	learn: 0.6974484	total: 1m 1s	remaining: 14.8s
644:	learn: 0.6974484	total: 1m 1s	remaining: 14.7s
645:	learn: 0.6974484	total: 1m 1s	remaining: 14.6s
646:	learn: 0.6974484	total: 1m 1s	remaining: 14.6s
647:	learn: 0.6974484	total: 1m 1s	remaining: 14.5s
648:	learn: 0.6974484	total: 1m 1s	remaining: 14.4s
649:	learn: 0.6974484	total: 1m 1s	remaining: 14.3s
650:	learn: 0.6974484	total: 1m 1s	remaining: 14.2s
651:	learn: 0.6974484	total: 1m 1s	remaining: 14.1s
652:	learn: 0.6974484	total: 1m 2s	remaining: 14s
653:	learn: 0.6966019	total: 1m 2s	remaining: 13.9s
654:	learn: 0.6974484	total: 1m 2s	remaining: 13.8s
655:	learn: 0.6974484	total: 1m 2s	remaining: 13.7s
656:	learn: 0.6974484	total: 1m 2s	remaining: 13.6s
657:	learn: 0.6974484	

796:	learn: 0.7073171	total: 1m 15s	remaining: 284ms
797:	learn: 0.7073171	total: 1m 15s	remaining: 189ms
798:	learn: 0.7064555	total: 1m 15s	remaining: 94.6ms
799:	learn: 0.7064555	total: 1m 15s	remaining: 0us


col_0   0.0  1.0
m13             
0      3990   11
1        57   70

In [68]:
print (classification_report(test_label,predict_cb))

              precision    recall  f1-score   support

           0       0.99      1.00      0.99      4001
           1       0.86      0.55      0.67       127

   micro avg       0.98      0.98      0.98      4128
   macro avg       0.93      0.77      0.83      4128
weighted avg       0.98      0.98      0.98      4128



In [124]:
pred = model_cb.predict(test)
pred = pred.flatten()
d={'loan_id':test1['loan_id'],'m13':pred}
ans=pd.DataFrame(d)
ans.to_csv('submission1.csv',index=False)

In [125]:
pred = rfc.predict(test)
pred = pred.flatten()
d={'loan_id':test1['loan_id'],'m13':pred}
ans=pd.DataFrame(d)
ans.to_csv('submission2.csv',index=False)

In [126]:
subm = pd.read_csv('submission2.csv')

In [127]:
subm['m13'].value_counts()

0    35674
1      192
Name: m13, dtype: int64

In [128]:
subm1 = pd.read_csv('submission1.csv')

In [130]:
subm1['m13'] = subm['m13']  + subm1['m13']

In [132]:
subm1['m13'].value_counts()

0.0    35670
2.0      178
1.0       18
Name: m13, dtype: int64

In [134]:
#combining multiple algorithms to get more accurate results
subm1['m13'] = subm1['m13'].replace([2.0,1.0],[1.0,0.0])

In [136]:
subm1.to_csv('submission3.csv',index=False)

In [138]:
subm1['m13'].value_counts()

0.0    35688
1.0      178
Name: m13, dtype: int64